# Downloading Dataset

In [0]:
!wget --header="Host: storage.googleapis.com" --header="User-Agent: Mozilla/5.0 (Windows NT 10.0; Win64; x64) AppleWebKit/537.36 (KHTML, like Gecko) Chrome/74.0.3729.169 Safari/537.36" --header="Accept: text/html,application/xhtml+xml,application/xml;q=0.9,image/webp,image/apng,*/*;q=0.8,application/signed-exchange;v=b3" --header="Accept-Language: en-US,en;q=0.9" --header="Referer: https://www.kaggle.com/" "https://storage.googleapis.com/kaggle-datasets/122892/296485/celebrities-100k.zip?GoogleAccessId=web-data@kaggle-161607.iam.gserviceaccount.com&Expires=1560782703&Signature=N0oUFHkZRVlHnbRzN76CQys5H3voggfGy%2BH8qFwmtPl69T5YiV3z%2BNK8KnFRhXwbyMYubyPfqfYxRHlnaJsbLPhUGB7%2BuTcX%2FdMdDv6GLTclwSYLPxnY7IcMdAXUiQd39kTryd5PDNRHNVyBOWjZHGnHFM2rldOWAUIgpmZ3GXzJ%2BJJq4i%2Br%2FxcufyhuSznah5algeuEhdX2imDeXc3ka%2BJHw6lLzLha7LyYLTGc%2B%2FVpStaMeki1OHNqc0qxpBRQ446MPr5O%2F4voI0GfmZHu02EZm00Emo4tHWbzx2bPU1%2BgBabEbRd4jj43pBBz0tFN8z0SVUTgzx%2BAJCHjUA6oLg%3D%3D" -O "celebrities-100k.zip" -c

--2019-06-14 14:45:18--  https://storage.googleapis.com/kaggle-datasets/122892/296485/celebrities-100k.zip?GoogleAccessId=web-data@kaggle-161607.iam.gserviceaccount.com&Expires=1560782703&Signature=N0oUFHkZRVlHnbRzN76CQys5H3voggfGy%2BH8qFwmtPl69T5YiV3z%2BNK8KnFRhXwbyMYubyPfqfYxRHlnaJsbLPhUGB7%2BuTcX%2FdMdDv6GLTclwSYLPxnY7IcMdAXUiQd39kTryd5PDNRHNVyBOWjZHGnHFM2rldOWAUIgpmZ3GXzJ%2BJJq4i%2Br%2FxcufyhuSznah5algeuEhdX2imDeXc3ka%2BJHw6lLzLha7LyYLTGc%2B%2FVpStaMeki1OHNqc0qxpBRQ446MPr5O%2F4voI0GfmZHu02EZm00Emo4tHWbzx2bPU1%2BgBabEbRd4jj43pBBz0tFN8z0SVUTgzx%2BAJCHjUA6oLg%3D%3D
Resolving storage.googleapis.com (storage.googleapis.com)... 74.125.69.128, 2607:f8b0:4001:c12::80
Connecting to storage.googleapis.com (storage.googleapis.com)|74.125.69.128|:443... connected.
HTTP request sent, awaiting response... 200 OK
Length: 860082689 (820M) [application/zip]
Saving to: ‘celebrities-100k.zip’

celebrities-100k.zi 100%[===================>] 820.24M  89.9MB/s    in 8.6s    

2019-06-14 14:45:27 (95.9 M

In [0]:
!unzip 'celebrities-100k.zip'

Archive:  celebrities-100k.zip
  inflating: 100k.zip                
  inflating: 100k.txt                


In [0]:
!unzip '100k.zip'

Archive:  100k.zip
   creating: 100k/
  inflating: 100k/110369.jpg         
  inflating: 100k/161590.jpg         
  inflating: 100k/065084.jpg         
  inflating: 100k/045354.jpg         
  inflating: 100k/126803.jpg         
  inflating: 100k/192418.jpg         
  inflating: 100k/151453.jpg         
  inflating: 100k/185164.jpg         
  inflating: 100k/013112.jpg         
  inflating: 100k/081470.jpg         
  inflating: 100k/055147.jpg         
  inflating: 100k/043725.jpg         
  inflating: 100k/101264.jpg         
  inflating: 100k/097212.jpg         
  inflating: 100k/074189.jpg         
  inflating: 100k/193706.jpg         
  inflating: 100k/005770.jpg         
  inflating: 100k/147231.jpg         
  inflating: 100k/054259.jpg         
  inflating: 100k/116718.jpg         
  inflating: 100k/098121.jpg         
  inflating: 100k/109638.jpg         
  inflating: 100k/087001.jpg         
  inflating: 100k/111077.jpg         
  inflating: 100k/062933.jpg         
  inflating:

# Building Model and Training

In [0]:
!mkdir 'Model Architecture images_deeper_network'

In [0]:
from __future__ import print_function, division

from keras.layers import Dense, Dropout, Flatten, Reshape, Input, BatchNormalization, Activation, ZeroPadding2D, MaxPooling2D, AveragePooling2D
from keras.layers.advanced_activations import LeakyReLU
from keras.layers.convolutional import UpSampling2D, Conv2D
from keras.models import Model, Sequential
from keras.optimizers import Adam
from PIL import Image
from keras.utils import plot_model
from numpy import random

import matplotlib.pyplot as plt
import numpy as np
import sys
import os as os
import tensorflow as tf

Using TensorFlow backend.


In [0]:
noise_shape = 100
nh = 64
nw = 64
nc = 3
img_shape = (nh, nw, nc)

# Carefully chosen parameters 
d_opt = Adam(lr = 0.00004, beta_1 = 0.5)
g_opt = Adam(lr = 0.0002, beta_1 = 0.5)

In [0]:
def build_generator():
  
  model = Sequential()
  model.add(Dense(128 * 4 * 4, input_dim = noise_shape, name = 'Dense_Layer'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_Dense'))
  model.add(Reshape((4, 4, 128) , name = "Reshape_Layer"))
  
  #
  model.add(Conv2D(128, kernel_size=3,  padding="same", name = "Conv_Layer"))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU'))
  model.add(BatchNormalization(momentum=0.8, name = "Batch_Norm"))
  #
  
  model.add(UpSampling2D(name = 'UpSampling_Layer_2'))
  model.add(Conv2D(64, kernel_size=3,  padding="same", name = "Conv_Layer_2"))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_2'))
  model.add(BatchNormalization(momentum=0.8, name = "Batch_Norm_2"))
  
  model.add(UpSampling2D(name = 'UpSampling_Layer_3'))
  model.add(Conv2D(32, kernel_size=3, padding="same", name = 'Conv_Layer_3'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_3'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_3'))
  
  model.add(UpSampling2D(name = 'UpSampling_Layer_4'))
  model.add(Conv2D(16, kernel_size=3, padding="same", name = 'Conv_Layer_4'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_4'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_4'))
  
  model.add(UpSampling2D(name = 'UpSampling_Layer_5'))
  model.add(Conv2D(8, kernel_size=3, padding="same", name = 'Conv_Layer_5'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_5'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_5'))
  
  model.add(Conv2D(4, kernel_size=3, padding="same", name = 'Conv_Layer_6'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_6'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_6'))
  
  model.add(Conv2D(3, kernel_size=3, padding="same", name = 'Conv_Layer_7'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_7'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_7'))
  model.add(Activation("tanh"))
   
  print(model.summary())
  
  #Picturizing model
  plot_model(model, to_file='Model Architecture images_deeper_network/generator.png')
  
  noise = Input(shape = (noise_shape,))
  img = model(noise)
  
  return Model(inputs = noise, outputs = img, name = "Generator")
  

In [0]:
generator = build_generator()
generator.summary()

W0614 14:42:32.307550 139711945439104 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:74: The name tf.get_default_graph is deprecated. Please use tf.compat.v1.get_default_graph instead.

W0614 14:42:32.311057 139711945439104 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:517: The name tf.placeholder is deprecated. Please use tf.compat.v1.placeholder instead.

W0614 14:42:32.315191 139711945439104 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:4138: The name tf.random_uniform is deprecated. Please use tf.random.uniform instead.

W0614 14:42:32.373717 139711945439104 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/backend/tensorflow_backend.py:174: The name tf.get_default_session is deprecated. Please use tf.compat.v1.get_default_session instead.

W0614 14:42:32.374689 1397119454

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
Dense_Layer (Dense)          (None, 2048)              206848    
_________________________________________________________________
Leaky_ReLU_Dense (LeakyReLU) (None, 2048)              0         
_________________________________________________________________
Reshape_Layer (Reshape)      (None, 4, 4, 128)         0         
_________________________________________________________________
Conv_Layer (Conv2D)          (None, 4, 4, 128)         147584    
_________________________________________________________________
Leaky_ReLU (LeakyReLU)       (None, 4, 4, 128)         0         
_________________________________________________________________
Batch_Norm (BatchNormalizati (None, 4, 4, 128)         512       
_________________________________________________________________
UpSampling_Layer_2 (UpSampli (None, 8, 8, 128)         0         
__________

In [0]:
def build_discriminator():
  model = Sequential()
  
  model.add(Conv2D(4, kernel_size=3, input_shape = img_shape, padding="same", name = 'Conv_Layer'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm'))
  
  model.add(Conv2D(8, kernel_size=3, strides = 2, name = 'Conv_Layer_2'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_2'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_2'))
  
  model.add(Conv2D(16, kernel_size=3, strides = 2, name = 'Conv_Layer_3'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_3'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_3'))
  
  model.add(Conv2D(32, kernel_size=3, strides = 2, name = 'Conv_Layer_4'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_4'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_4'))
  
  model.add(Conv2D(64, kernel_size=2, strides = 1, name = 'Conv_Layer_5'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_5'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_5'))
  
  #
  model.add(Conv2D(128, kernel_size=2, strides = 1, name = 'Conv_Layer_6'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_6'))
  model.add(BatchNormalization(momentum=0.8, name = 'Batch_Norm_6'))
  #
  
  model.add(Flatten(name = 'Flatten'))
  model.add(Dense(512, name = 'Dense_Layer'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_7'))
  
  model.add(Dense(256, name = 'Dense_Layer_2'))
  model.add(LeakyReLU(alpha=0.2, name = 'Leaky_ReLU_8'))
  model.add(Dense(1, activation='sigmoid', name = 'Dense_with_Sigmoid'))
  
  print(model.summary())
  
  #Picturizing model
  plot_model(model, to_file='Model Architecture images_deeper_network/discriminator.png')
  
  img = Input(shape = img_shape)
  validity = model(img)
  
  return Model(inputs = img, outputs = validity, name = 'Discriminator')

In [0]:
discriminator = build_discriminator()
discriminator.summary()

discriminator.compile(loss = 'binary_crossentropy', optimizer = d_opt, metrics = ['accuracy'])

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
Conv_Layer (Conv2D)          (None, 64, 64, 4)         112       
_________________________________________________________________
Leaky_ReLU (LeakyReLU)       (None, 64, 64, 4)         0         
_________________________________________________________________
Batch_Norm (BatchNormalizati (None, 64, 64, 4)         16        
_________________________________________________________________
Conv_Layer_2 (Conv2D)        (None, 31, 31, 8)         296       
_________________________________________________________________
Leaky_ReLU_2 (LeakyReLU)     (None, 31, 31, 8)         0         
_________________________________________________________________
Batch_Norm_2 (BatchNormaliza (None, 31, 31, 8)         32        
_________________________________________________________________
Conv_Layer_3 (Conv2D)        (None, 15, 15, 16)        1168      
__________

W0614 14:42:37.812194 139711945439104 deprecation_wrapper.py:119] From /usr/local/lib/python3.6/dist-packages/keras/optimizers.py:790: The name tf.train.Optimizer is deprecated. Please use tf.compat.v1.train.Optimizer instead.

W0614 14:42:37.825596 139711945439104 deprecation.py:323] From /usr/local/lib/python3.6/dist-packages/tensorflow/python/ops/nn_impl.py:180: add_dispatch_support.<locals>.wrapper (from tensorflow.python.ops.array_ops) is deprecated and will be removed in a future version.
Instructions for updating:
Use tf.where in 2.0, which has the same broadcast rule as np.where


_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 64, 64, 3)         0         
_________________________________________________________________
sequential_2 (Sequential)    (None, 1)                 1818873   
Total params: 1,818,873
Trainable params: 1,818,369
Non-trainable params: 504
_________________________________________________________________


In [0]:
z = Input(shape = (noise_shape,), name = "Input_Noise")
img = generator(z)

discriminator.trainable = False
valid = discriminator(img)

combined = Model(z, valid)
combined.compile(loss = 'binary_crossentropy', optimizer = g_opt)
combined.summary()

#Picturizing model
plot_model(combined, to_file='Model Architecture images_deeper_network/combined.png')

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
Input_Noise (InputLayer)     (None, 100)               0         
_________________________________________________________________
Generator (Model)            (None, 64, 64, 3)         453895    
_________________________________________________________________
Discriminator (Model)        (None, 1)                 1818873   
Total params: 2,272,768
Trainable params: 453,385
Non-trainable params: 1,819,383
_________________________________________________________________


In [0]:
print(generator.summary())
print(discriminator.summary())
print(combined.summary())

_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_1 (InputLayer)         (None, 100)               0         
_________________________________________________________________
sequential_1 (Sequential)    (None, 64, 64, 3)         453895    
Total params: 453,895
Trainable params: 453,385
Non-trainable params: 510
_________________________________________________________________
None
_________________________________________________________________
Layer (type)                 Output Shape              Param #   
input_2 (InputLayer)         (None, 64, 64, 3)         0         
_________________________________________________________________
sequential_2 (Sequential)    (None, 1)                 1818873   
Total params: 3,637,242
Trainable params: 1,818,369
Non-trainable params: 1,818,873
_________________________________________________________________
None
________________________________________

/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


In [0]:
def get_batch(width, height):
  image_files = os.listdir('/content/100k/')
  data_batch = []
  
  for file in image_files:
    img = Image.open('/content/100k/'+file).resize([width, height])
    data_batch.append(np.array(img.convert('RGB')))
    
  data_batch = np.array(data_batch)
  print(data_batch.shape)
  return data_batch

In [0]:
def train(batch_size = 128, epochs = 15830):
  
  
  valid = np.ones((batch_size, 1))
  fakes = np.zeros((batch_size, 1))
  
  X_train = get_batch(nw, nh)
  X_train = (X_train.astype(np.float32) - 127.5) / 127.5
  
  for epoch in range(epochs):
    
    idx = np.random.randint(0, X_train.shape[0], batch_size)
    imgs = X_train[idx]
    
    noise = np.random.normal(0, 1, (batch_size, noise_shape))
    
    gen_imgs = generator.predict(noise)

    #Training Discriminator
    d_loss_real = discriminator.train_on_batch(imgs, valid)
    d_loss_fake = discriminator.train_on_batch(gen_imgs, fakes)
    d_loss = 0.5*np.add(d_loss_real, d_loss_fake)

    #Training Generator
    g_loss = combined.train_on_batch(noise, valid)

    #Progress
    if (epoch+1)%50 == 0:
      print("epoch: " + str(epoch+1) + " " + "D_Loss = " + str(d_loss[0]) + " " + "acc: " + str(d_loss[1]*100) + " " +  "G_Loss = " + str(g_loss))
    
    if (epoch+1)%10000 == 0 or epoch+1 == 1000:
      save_imgs(epoch+1)

In [0]:
!mkdir 'images_deeper_network'

In [0]:
def save_imgs(epoch):
  r, c = 3, 3
  noise = np.random.normal(0, 1, (r * c, noise_shape))
  gen_imgs = generator.predict(noise)

  # Rescale images 0 - 1
  gen_imgs = (1/2.5) * gen_imgs + 0.5
  
  fig, axs = plt.subplots(r, c)
  cnt = 0
  for i in range(r):
      for j in range(c):
          axs[i,j].imshow(gen_imgs[cnt, :,:,:])
          axs[i,j].axis('off')
          cnt += 1
  fig.savefig("images_deeper_network/%d.png" % epoch)
  plt.close()

In [0]:
#generator.load_weights('generator.h5')
#discriminator.load_weights('discriminator.h5')

In [0]:
train(128, 100000)

(100000, 64, 64, 3)


/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'
/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'
/usr/local/lib/python3.6/dist-packages/keras/engine/training.py:490: UserWarning: Discrepancy between trainable weights and collected trainable weights, did you set `model.trainable` without calling `model.compile` after ?
  'Discrepancy between trainable weights and collected trainable'


epoch: 50 D_Loss = 0.26827583 acc: 89.84375 G_Loss = 1.935977
epoch: 100 D_Loss = 0.18791156 acc: 94.921875 G_Loss = 2.4693744
epoch: 150 D_Loss = 0.15918441 acc: 93.75 G_Loss = 3.0025887
epoch: 200 D_Loss = 0.12434452 acc: 96.09375 G_Loss = 3.291729
epoch: 250 D_Loss = 0.22816482 acc: 92.578125 G_Loss = 3.035049
epoch: 300 D_Loss = 0.2522531 acc: 89.84375 G_Loss = 3.1410458
epoch: 350 D_Loss = 0.26589227 acc: 88.671875 G_Loss = 3.0485845
epoch: 400 D_Loss = 0.3500104 acc: 83.59375 G_Loss = 2.695498
epoch: 450 D_Loss = 0.3640744 acc: 85.15625 G_Loss = 2.4226787
epoch: 500 D_Loss = 0.34695446 acc: 83.984375 G_Loss = 2.262547
epoch: 550 D_Loss = 0.40726274 acc: 82.421875 G_Loss = 2.2697392
epoch: 600 D_Loss = 0.46366036 acc: 77.734375 G_Loss = 1.968612
epoch: 650 D_Loss = 0.3829738 acc: 83.59375 G_Loss = 2.1200275
epoch: 700 D_Loss = 0.40703884 acc: 82.03125 G_Loss = 1.9084039
epoch: 750 D_Loss = 0.33268547 acc: 85.9375 G_Loss = 2.2232995
epoch: 800 D_Loss = 0.3981606 acc: 82.8125 G_Loss

# Generating Images

In [0]:
save_imgs(100002)

In [0]:
noise = np.random.normal(0, 1, (1, noise_shape))
gen_imgs = generator.predict(noise)
gen_imgs = gen_imgs*(1/2.5) + 0.5

plt.imshow(gen_imgs.reshape((64 , 64, 3)))

In [0]:
generator.save_weights('generator.h5')
discriminator.save_weights('discriminator.h5')